# Tutorial 51: Manual Creation of Element Dataframes

This Example demonstrates the capabilities of the class Dataframes_SIR3S_Model that extends SIR3S_Model be abilities to work directley with pandas dataframes. It is shown how to create dataframes containing information about elements such as Nodes, Pipes, etc. existing in a SIR 3S Model. The methods presented are manual, user-defined and detailed. For creating more general dataframes with less input necessary, see Tutorial 52.   

# Toolkit Release

In [1]:
#pip install 

# Imports

## SIR 3S Toolkit

### Regular Import/Init

In [2]:
SIR3S_SIRGRAF_DIR = r"C:\3S\SIR 3S\SirGraf-90-15-00-20x64_Quebec-Upd1" #change to local path

In [3]:
from sir3stoolkit.core import wrapper

In [4]:
wrapper

<module 'sir3stoolkit.core.wrapper' from 'C:\\Users\\aUsername\\3S\\sir3stoolkit\\src\\sir3stoolkit\\core\\wrapper.py'>

In [5]:
wrapper.Initialize_Toolkit(SIR3S_SIRGRAF_DIR)

### Additional Import/Init for Dataframes class

In [6]:
from sir3stoolkit.mantle.dataframes import SIR3S_Model_Dataframes

In [7]:
s3s = SIR3S_Model_Dataframes()

Initialization complete


## Additional

In [8]:
import pandas as pd
from shapely.geometry import Point
import re
import folium
from folium.plugins import HeatMap
import numpy as np
import geopandas as gpd
from shapely import wkt
import matplotlib.pyplot as plt
import contextily as cx

# Open Model

In [9]:
s3s.OpenModel(dbName=r"C:\Users\aUsername\3S\PT3S\PT3S\Examples\Example3.db3",
              providerType=s3s.ProviderTypes.SQLite,
              Mid="M-1-0-1",
              saveCurrentlyOpenModel=False,
              namedInstance="",
              userID="",
              password="")

Model is open for further operation


# Manual Dataframe creation

## model_data - Nodes

We can use the [generate_element_model_data_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_model_data_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined model_data properties (all non-result data related to a component) to be added. For this example we will use nodes.

In this case we are interested in Nodes, let's check what model_data properties are available for this element.

In [10]:
s3s.GetPropertiesofElementType(s3s.ObjectTypes.Node)

['Name',
 'Ktyp',
 'Zkor',
 'QmEin',
 'Lfakt',
 'Fkpzon',
 'Fkfstf',
 'Fkutmp',
 'Fkfqps',
 'Fkcont',
 'Fk2lknot',
 'Beschreibung',
 'Idreferenz',
 'Iplanung',
 'Kvr',
 'Qakt',
 'Xkor',
 'Ykor',
 'NodeNamePosition',
 'ShowNodeName',
 'KvrKlartext',
 'NumberOfVERB',
 'HasBlockConnection',
 'Tk',
 'Pk',
 'InVariant',
 'GeometriesDiffer',
 'SymbolFactor',
 'bz.Drakonz',
 'bz.Fk',
 'bz.Fkpvar',
 'bz.Fkqvar',
 'bz.Fklfkt',
 'bz.PhEin',
 'bz.Tm',
 'bz.Te',
 'bz.PhMin']

In the below subcases differnt choices of parameters for creating the model_data dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Minimal

Let's say for now we only want a dataframe with all node tks without any related data.

In [11]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        )).head(3)

[2026-01-09 16:08:42,734] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-01-09 16:08:42,741] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-01-09 16:08:42,762] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 0 model_data properties.
[2026-01-09 16:08:42,762] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving ...
[2026-01-09 16:08:42,767] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 1)


tk
0  5669301360686511351
1  5397948523091900401
2  5239335112004772156

### Subcase 2: Specific Properties 

Let's say we now want the minimal dataframe extended with supply/return info (kvr) and height (Zkor) of the nodes.

In [12]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=["Kvr", "Zkor"]
                                        )).head(3)

[2026-01-09 16:08:42,795] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-01-09 16:08:42,799] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-01-09 16:08:42,802] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 2 model_data properties.
[2026-01-09 16:08:42,803] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['Kvr', 'Zkor']...
[2026-01-09 16:08:42,900] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 3)


tk  Kvr    Zkor
0  5669301360686511351    1  554.04
1  5397948523091900401    1  556.16
2  5239335112004772156    1  561.01

### Subcase 3: Maximal

Let's say now we want basically all available model_data (non-result data) related to nodes. 

If geometry=True, the 2D Point geometry will be added for Nodes and it will be attempted to transform the DataFrame into a GeoDataFrame using the SRID (eg. EPSG: 25832) defined in the model. If no SRID is defined, the DataFrame will remain as a DataFrame, but the geometry column with be added nonetheless.

In [13]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=None # Instead of an empty or filled list, we pass None to indicate we want all available properties
                                        ,geometry=True # geometry data has to be explicitly requested
                                        )).head(3)

[2026-01-09 16:08:42,929] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-01-09 16:08:42,933] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-01-09 16:08:42,936] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] No properties given → using ALL model_data properties for ObjectTypes.Node.
[2026-01-09 16:08:42,937] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 37 model_data properties.
[2026-01-09 16:08:42,939] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['Name', 'Ktyp', 'Zkor', 'QmEin', 'Lfakt', 'Fkpzon', 'Fkfstf', 'Fkutmp', 'Fkfqps', 'Fkcont', 'Fk2lknot', 'Beschreibung', 'Idreferenz', 'Iplanung', 'Kvr', 'Qakt', 'Xkor', 'Ykor', 'NodeNamePosition', 'ShowNodeName', 'KvrKlartext', 'NumberOfVERB', 'HasBlockConnection', 'Tk', 'Pk', 'InVariant', 'Geo

tk    Name  Ktyp    Zkor  QmEin  Lfakt  \
0  5669301360686511351  V-K03S  QKON  554.04      0      1   
1  5397948523091900401  V-K13S  QKON  556.16      0      1   
2  5239335112004772156  V-K23S  QKON  561.01      0      1   

                Fkpzon               Fkfstf               Fkutmp  Fkfqps  \
0  5520728169779652386  4798673252636751115  5591325053703727727      -1   
1  5520728169779652386  4798673252636751115  5591325053703727727      -1   
2  5520728169779652386  4798673252636751115  5591325053703727727      -1   

                Fkcont             Fk2lknot  \
0  5029128874972463118  5761544923588724980   
1  5029128874972463118  4749864932928780363   
2  5029128874972463118  4899862460906451371   

                        Beschreibung                          Idreferenz  \
0                Abzw. Am Sonnenbühl  3S3768E2953006F125B34916F6A1681667   
1  Anfangsknoten generiert von SirDB  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B   
2  Anfangsknoten generiert von SirDB  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B   

   Iplanung  Kvr  Qakt           Xkor          Ykor  NodeNamePosition  \
0         1    1     0  713620.267807  5.578828e+06                 1   
1         1    1     0  713602.294600  5.578860e+06                 1   
2         1    1     0  713574.061627  5.578910e+06                 1   

  ShowNodeName KvrKlartext  NumberOfVERB HasBlockConnection  \
0        False     Vorlauf             0              False   
1        False     Vorlauf             0              False   
2        False     Vorlauf             0              False   

                    Tk                   Pk InVariant GeometriesDiffer  \
0  5669301360686511351  5669301360686511351     False            False   
1  5397948523091900401  5397948523091900401     False            False   
2  5239335112004772156  5239335112004772156     False            False   

   SymbolFactor  bz.Drakonz                bz.Fk  bz.Fkpvar  bz.Fkqvar  \
0           0.2           0  5669301360686511351         -1         -1   
1           0.2           0  5397948523091900401         -1         -1   
2           0.2           0  5239335112004772156         -1         -1   

   bz.Fklfkt  bz.PhEin  bz.Tm  bz.Te  bz.PhMin                        geometry  
0         -1         0      0      0         0  POINT (713620.268 5578828.419)  
1         -1         0      0      0         0  POINT (713602.295 5578860.106)  
2         -1         0      0      0         0  POINT (713574.062 5578909.873)

### Subcase 4: Filtering + Element Type Col

Let's say we only want nodes inside a specific container and we also want to have an element type col adding "Node" to each row (useful when joining with other dataframes later).

In [14]:
for container_id in (s3s.GetTksofElementType(s3s.ObjectTypes.ObjectContainerSymbol)):
    print(f"{container_id}: {s3s.GetValue(container_id, 'Name')[0]}")

5029128874972463118: M-1-0-1
5027846505677995694: Erzeugung
5172832702839270493: TS
5152808213068069018: Laststeuerung
5467315850619588583: Sekundärwerte
5320319133990336755: Netztrennung


In [15]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Node)

In [16]:
good_tks = []

In [17]:
for tk in all_tks:
    if s3s.GetValue(tk, "FkCont") == "5029128874972463118": # Main container
        if s3s.GetValue(tk, "Kvr")[0] == "1": # Supply/Vorlauf
            good_tks.append(tk)

In [18]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        ,tks=good_tks
                                        ,geometry=True
                                        ,element_type_col=True
                                        )).head(3)

[2026-01-09 16:08:45,432] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-01-09 16:08:45,437] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-01-09 16:08:45,440] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 0 model_data properties.
[2026-01-09 16:08:45,441] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving geometry...
[2026-01-09 16:08:45,512] INFO in sir3stoolkit.mantle.dataframes: [model_data] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2026-01-09 16:08:45,513] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 3)


tk                        geometry element type
0  5669301360686511351  POINT (713620.268 5578828.419)         Node
1  5397948523091900401  POINT (713602.295 5578860.106)         Node
2  5239335112004772156  POINT (713574.062 5578909.873)         Node

## Result Data - Pipes

We can use the [generate_element_model_data_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_results_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined result values for certain timestamps to be added. For this example we will use pipes.

Let's check what result properties are available for Pipes.

In [19]:
s3s.GetResultProperties_from_elementType(elementType=s3s.ObjectTypes.Pipe
                                         ,onlySelectedVectors=False 
                                         )

['A',
 'ACALC',
 'CPI',
 'CPK',
 'DH',
 'DP',
 'DRAGRED',
 'DRAKONZ',
 'DSI',
 'DSK',
 'DTTR',
 'DWVERL',
 'DWVERLABS',
 'ETAAV',
 'FS',
 'HR',
 'HVEC',
 'IAKTIV',
 'IRTRENN',
 'JV',
 'JV2',
 'LAMBDA',
 'LECKEINAUS',
 'LECKMENGE',
 'LECKORT',
 'LINEPACK',
 'LINEPACKGEOM',
 'LINEPACKRATE',
 'MAINELEMENT',
 'MAV',
 'MI',
 'MK',
 'MKOND',
 'MMAX_INST',
 'MMIN_INST',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PAV',
 'PDAMPF',
 'PHR',
 'PHVEC',
 'PMAX',
 'PMIN',
 'PR',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QI2',
 'QK2',
 'QMAV',
 'QMI',
 'QMK',
 'QMMAX_INST',
 'QMMIN_INST',
 'QMVEC',
 'QSVB',
 'RHOAV',
 'RHOI',
 'RHOK',
 'RHOVEC',
 'SVEC',
 'TAV',
 'TI',
 'TK',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'VAV',
 'VI',
 'VK',
 'VMAX_INST',
 'VMIN_INST',
 'VOLDA',
 'WALTERI',
 'WALTERK',
 'WVL',
 'ZAUS',
 'ZEIN',
 'ZHKNR',
 'ZVEC']

Let's also check what simulation timestamps are available in the model.

In [20]:
s3s.GetTimeStamps()[0] # list of simulation timestamps

['2023-02-13 00:00:00.000 +01:00',
 '2023-02-13 01:00:00.000 +01:00',
 '2023-02-13 02:00:00.000 +01:00',
 '2023-02-13 03:00:00.000 +01:00',
 '2023-02-13 04:00:00.000 +01:00',
 '2023-02-13 05:00:00.000 +01:00',
 '2023-02-13 06:00:00.000 +01:00',
 '2023-02-13 07:00:00.000 +01:00',
 '2023-02-13 08:00:00.000 +01:00',
 '2023-02-13 09:00:00.000 +01:00',
 '2023-02-13 10:00:00.000 +01:00',
 '2023-02-13 11:00:00.000 +01:00',
 '2023-02-13 12:00:00.000 +01:00',
 '2023-02-13 13:00:00.000 +01:00',
 '2023-02-13 14:00:00.000 +01:00',
 '2023-02-13 15:00:00.000 +01:00',
 '2023-02-13 16:00:00.000 +01:00',
 '2023-02-13 17:00:00.000 +01:00',
 '2023-02-13 18:00:00.000 +01:00',
 '2023-02-13 19:00:00.000 +01:00',
 '2023-02-13 20:00:00.000 +01:00',
 '2023-02-13 21:00:00.000 +01:00',
 '2023-02-13 22:00:00.000 +01:00',
 '2023-02-13 23:00:00.000 +01:00',
 '2023-02-14 00:00:00.000 +01:00']

In [21]:
s3s.GetTimeStamps()[1] # Static

'2023-02-13 00:00:00.000 +01:00'

In the below subcases differnt choices of parameters for creating the result dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Static + All Result Values

In [ ]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=None # None => All available properties
                                        ,timestamps=[s3s.GetTimeStamps()[1]] # static
                                        )).head(3)

[2026-01-09 16:25:57,497] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:25:57,571] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2026-01-09 16:25:57,572] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2026-01-09 16:25:57,574] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:25:57,575] INFO in sir3stoolkit.mantle.dataframes: [results] No properties given → using ALL result properties for ObjectTypes.Pipe.
[2026-01-09 16:25:57,576] INFO in sir3stoolkit.mantle.dataframes: [results] Using 82 result properties.
[2026-01-09 16:25:57,605] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:26:09,632] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: 

Note that a multi index on the columns is created, holding the most important model_data.
- Level 0: tk (device ID)
- Level 1: name (device name)
- Level 2: end_nodes (tuple of connected node IDs as string)
- Level 3: property (result name)

As can be seen a lot of 99999.0 placeholder values are inserted, because we attempt to access many result values that SIR Calc can calculate but are not requested for this model. Therefore using all available result properties(properties=None), is generally not recommended.

### Subcase 2: All Timestamps + Specific Values

In [86]:
df_pipes_2 = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                    ,properties=["DTTR", "PHR"] # Specify result properties of interest
                                                    ,timestamps=None # None => All available simulation timestamps
                                                    )

[2026-01-09 16:27:35,278] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:27:35,280] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] No timestamps were given. Checking available simulation timestamps (SIR3S_Model.GetTimeStamps()[0]).
[2026-01-09 16:27:35,511] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 simulation timestamp(s) are available.
[2026-01-09 16:27:35,663] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 valid timestamp(s) will be used.
[2026-01-09 16:27:35,667] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:27:35,670] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-01-09 16:27:35,724] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:27:45,029] INFO in sir3stoolkit.mantle.dataframes: 

In [87]:
df_pipes_2.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 01:00:00.000 +01:00                                           0.013283           
2023-02-13 02:00:00.000 +01:00                                           0.013074           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 01:00:00.000 +01:00  0.010654   
2023-02-13 02:00:00.000 +01:00  0.010982   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 01:00:00.000 +01:00                                           0.025093           
2023-02-13 02:00:00.000 +01:00                                           0.024704           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 01:00:00.000 +01:00  0.014936   
2023-02-13 02:00:00.000 +01:00  0.015388   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 01:00:00.000 +01:00                                           0.017629           
2023-02-13 02:00:00.000 +01:00                                           0.017354           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 01:00:00.000 +01:00  0.011113   
2023-02-13 02:00:00.000 +01:00  0.011451   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 01:00:00.000 +01:00                                           0.002938           
2023-02-13 02:00:00.000 +01:00                         

We can access individual values as follows.

In [88]:
df_pipes_2.loc[
    "2023-02-13 00:00:00.000 +01:00",
    ("5442010239090746007", slice(None), slice(None), "DTTR")
].item()


0.0134368

### Subcase 3: Specific Timestamps + Specific Values

We can specify the list of timestamps to include either as a list of str timestamps ...

In [24]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=['2023-02-13 00:00:00.000 +01:00', '2023-02-13 05:00:00.000 +01:00', '2023-02-13 23:00:00.000 +01:00'] 
                                        )).head(3)

[2026-01-09 16:09:04,311] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:09:04,562] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-01-09 16:09:04,565] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:09:04,568] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-01-09 16:09:04,603] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:09:05,385] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

... or as a list of int indices.

In [25]:
simulation_timestamps=s3s.GetTimeStamps()[0]

In [26]:
for idx, timestamp in enumerate(simulation_timestamps):
    print(idx, timestamp)

0 2023-02-13 00:00:00.000 +01:00
1 2023-02-13 01:00:00.000 +01:00
2 2023-02-13 02:00:00.000 +01:00
3 2023-02-13 03:00:00.000 +01:00
4 2023-02-13 04:00:00.000 +01:00
5 2023-02-13 05:00:00.000 +01:00
6 2023-02-13 06:00:00.000 +01:00
7 2023-02-13 07:00:00.000 +01:00
8 2023-02-13 08:00:00.000 +01:00
9 2023-02-13 09:00:00.000 +01:00
10 2023-02-13 10:00:00.000 +01:00
11 2023-02-13 11:00:00.000 +01:00
12 2023-02-13 12:00:00.000 +01:00
13 2023-02-13 13:00:00.000 +01:00
14 2023-02-13 14:00:00.000 +01:00
15 2023-02-13 15:00:00.000 +01:00
16 2023-02-13 16:00:00.000 +01:00
17 2023-02-13 17:00:00.000 +01:00
18 2023-02-13 18:00:00.000 +01:00
19 2023-02-13 19:00:00.000 +01:00
20 2023-02-13 20:00:00.000 +01:00
21 2023-02-13 21:00:00.000 +01:00
22 2023-02-13 22:00:00.000 +01:00
23 2023-02-13 23:00:00.000 +01:00
24 2023-02-14 00:00:00.000 +01:00


In [27]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        )).head(3)

[2026-01-09 16:09:06,709] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:09:06,859] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-01-09 16:09:06,864] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:09:06,868] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-01-09 16:09:06,906] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:09:07,918] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 4: Specific Timestamps + Specific Values + Filtering

If we want to filter for more than just the container, we have to filter tks outside the function and then pass them. Works same way as for model_data.

In [28]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Pipe)

In [29]:
len(all_tks)

524

In [30]:
good_tks = []

In [31]:
for tk in all_tks:
    if s3s.GetValue(tk, "FkCont")[0] == "5029128874972463118":
        if s3s.GetValue(tk, "bz.Irtrenn")[0] == "0": # Rohr nicht getrennt
            good_tks.append(tk)

In [32]:
len(good_tks)

480

In [33]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,tks=good_tks # here we specify that not all available tks should be used
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        )).head(3)

[2026-01-09 16:09:10,430] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:09:10,597] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-01-09 16:09:10,601] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:09:10,607] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 480 tks remain after filtering for given tks.
[2026-01-09 16:09:10,614] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-01-09 16:09:10,657] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:09:11,586] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 960)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 5: Specific Vectorized results + Specific Timestamps

For pipes we have interior point result values. These are usually found as vectors with the postfix VEC.

In [34]:
available_result_props=s3s.GetResultProperties_from_elementType(s3s.ObjectTypes.Pipe,False)

In [35]:
available_result_props

['A',
 'ACALC',
 'CPI',
 'CPK',
 'DH',
 'DP',
 'DRAGRED',
 'DRAKONZ',
 'DSI',
 'DSK',
 'DTTR',
 'DWVERL',
 'DWVERLABS',
 'ETAAV',
 'FS',
 'HR',
 'HVEC',
 'IAKTIV',
 'IRTRENN',
 'JV',
 'JV2',
 'LAMBDA',
 'LECKEINAUS',
 'LECKMENGE',
 'LECKORT',
 'LINEPACK',
 'LINEPACKGEOM',
 'LINEPACKRATE',
 'MAINELEMENT',
 'MAV',
 'MI',
 'MK',
 'MKOND',
 'MMAX_INST',
 'MMIN_INST',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PAV',
 'PDAMPF',
 'PHR',
 'PHVEC',
 'PMAX',
 'PMIN',
 'PR',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QI2',
 'QK2',
 'QMAV',
 'QMI',
 'QMK',
 'QMMAX_INST',
 'QMMIN_INST',
 'QMVEC',
 'QSVB',
 'RHOAV',
 'RHOI',
 'RHOK',
 'RHOVEC',
 'SVEC',
 'TAV',
 'TI',
 'TK',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'VAV',
 'VI',
 'VK',
 'VMAX_INST',
 'VMIN_INST',
 'VOLDA',
 'WALTERI',
 'WALTERK',
 'WVL',
 'ZAUS',
 'ZEIN',
 'ZHKNR',
 'ZVEC']

In [36]:
available_result_vector_props=[available_result_props for available_result_props in available_result_props if "VEC" in available_result_props]

In [37]:
available_result_vector_props

['HVEC',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PHVEC',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QMVEC',
 'RHOVEC',
 'SVEC',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'ZVEC']

In [79]:
df_pipes = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["TTRVEC", "MVEC", "DTTR"]
                                        ,timestamps=[0, 5, -2] 
                                        )

[2026-01-09 16:24:42,849] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:24:42,921] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-01-09 16:24:42,923] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:24:42,926] INFO in sir3stoolkit.mantle.dataframes: [results] Using 3 result properties.
[2026-01-09 16:24:42,941] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:24:43,650] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1572)


In [39]:
df_pipes.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00  0.3226847\t0.3260439\t0.3294031\t0.3327624\t0....           
2023-02-13 05:00:00.000 +01:00  0.2057737\t0.2079191\t0.2100645\t0.2122099\t0....           
2023-02-13 23:00:00.000 +01:00  0.3030474\t0.306203\t0.3093587\t0.3125143\t0.3...           

tk                                                                                \
name                                                                               
end_nodes                                                                          
property                                                                    MVEC   
timestamp                                                                          
2023-02-13 00:00:00.000 +01:00  14.68004\t14.68004\t14.68004\t14.68004\t14.68004   
2023-02-13 05:00:00.000 +01:00  22.98424\t22.98424\t22.98424\t22.98424\t22.98424   
2023-02-13 23:00:00.000 +01:00  15.62682\t15.62682\t15.62682\t15.62682\t15.62682   

tk                                        \
name                                       
end_nodes                                  
property                            DTTR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.013437   
2023-02-13 05:00:00.000 +01:00  0.008582   
2023-02-13 23:00:00.000 +01:00  0.012623   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00  0.3361216\t0.3403516\t0.3445816\t0.3488116\t0....           
2023-02-13 05:00:00.000 +01:00  0.2143553\t0.217069\t0.2197828\t0.2224965\t0.2...           
2023-02-13 23:00:00.000 +01:00  0.3156699\t0.3196465\t0.3236231\t0.3275996\t0....           

tk                                                                                 \
name                                                                                
end_nodes                                                                           
property                                                                     MVEC   
timestamp                                                                           
2023-02-13 00:00:00.000 +01:00  8.239944\t8.239944\t8.239944\t8.239944\t8.2399...   
2023-02-13 05:00:00.000 +01:00  12.843\t12.843\t12.843\t12.843\t12.843\t12.843...   
2023-02-13 23:00:00.000 +01:00  8.764987\t8.764987\t8.764987\t8.764987\t8.7649...   

tk                                        \
name                                       
end_nodes                                  
property                            DTTR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.025380   
2023-02-13 05:00:00.000 +01:00  0.016282   
2023-02-13 23:00:00.000 +01:00  0.023859   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                     

As can be seen, the vectorized result values are written as strings with "/" seperators. For better access we can extend these values to a multiindex using [add_interior_points_to_results_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.SIR3S_Model_Dataframes.add_interior_points_to_results_dataframe).

In [80]:
df_pipes_interior_points = s3s.add_interior_points_to_results_dataframe(df_pipes)

In [81]:
df_pipes_interior_points.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.322685           
2023-02-13 05:00:00.000 +01:00                                           0.205774           
2023-02-13 23:00:00.000 +01:00                                           0.303047           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.326044  0.329403  0.332762  0.336122   
2023-02-13 05:00:00.000 +01:00  0.207919  0.210064  0.212210  0.214355   
2023-02-13 23:00:00.000 +01:00  0.306203  0.309359  0.312514  0.315670   

tk                                                                      \
name                                                                     
end_nodes                                                                
property                            MVEC                                 
interior points                       0         1         2         3    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  14.68004  14.68004  14.68004  14.68004   
2023-02-13 05:00:00.000 +01:00  22.98424  22.98424  22.98424  22.98424   
2023-02-13 23:00:00.000 +01:00  15.62682  15.62682  15.62682  15.62682   

tk                                                  \
name                                                 
end_nodes                                            
property                                      DTTR   
interior points                       4        -1    
timestamp                                            
2023-02-13 00:00:00.000 +01:00  14.68004  0.013437   
2023-02-13 05:00:00.000 +01:00  22.98424  0.008582   
2023-02-13 23:00:00.000 +01:00  15.62682  0.012623   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.336122           
2023-02-13 05:00:00.000 +01:00                                           0.214355           
2023-02-13 23:00:00.000 +01:00                                           0.315670           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.340352  0.344582  0.34881

Note that an additional multiindex is created that indexes the interior points. Non-vectorized properties get index -1 in the new multiindex .

We can access individual values as follows.

In [82]:
df_pipes_interior_points.loc[
    "2023-02-13 00:00:00.000 +01:00",
    ("5442010239090746007", slice(None), slice(None), "MVEC", 2)
].item()


14.68004

## Merge model_data and Result Dataframes (for one timestamp)

### Create Dataframes - For pipes

#### model_data

In [41]:
df_pipes_model_data = s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                            ,properties=["L", "DN"]
                                                            ,geometry=True
                                                            )

[2026-01-09 16:09:25,212] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:09:25,212] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:09:25,212] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 2 model_data properties.
[2026-01-09 16:09:25,228] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['L', 'DN'], geometry...
[2026-01-09 16:09:25,426] INFO in sir3stoolkit.mantle.dataframes: [model_data] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2026-01-09 16:09:25,429] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (524, 4)


In [42]:
df_pipes_model_data.head(3)

tk         L   DN  \
0  5442010239090746007  36.42935  150   
1  4917786378639043296  57.21781  125   
2  4762482310382009633  40.99482  125   

                                            geometry  
0  LINESTRING (713620.268 5578828.419, 713602.295...  
1  LINESTRING (713602.295 5578860.106, 713574.062...  
2  LINESTRING (713574.062 5578909.873, 713553.84 ...

#### Results

In [43]:
df_pipes_results = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                        ,properties=["DTTR", "PHR"]
                                                        ,timestamps=[0] 
                                                        )

[2026-01-09 16:09:25,480] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-01-09 16:09:25,565] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2026-01-09 16:09:25,575] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2026-01-09 16:09:25,579] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-01-09 16:09:25,581] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-01-09 16:09:25,593] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-01-09 16:09:25,919] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (1, 1048)


In [44]:
df_pipes_results.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.001812   

tk                                                                    5722206630503885118  \
name                                                                   Rohr V-K43S V-K53S   
end_nodes                      ('4993257270457791438', '5317865645994989592', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.003259           

tk                                        \
name                                       
end_nodes                                  
property     

### Merge

In [45]:
df_pipes_results.columns = df_pipes_results.columns.droplevel([1, 2])
df_pipes_results = df_pipes_results.T.unstack(level=0).T
df_pipes_results = df_pipes_results.droplevel(0, axis=0)
df_pipes = df_pipes_model_data.merge(on="tk",
                    how="outer",
                    right=df_pipes_results)

In [46]:
df_pipes.head(3)

tk          L   DN  \
0  4614463970292122863   7.780674  999   
1  4615723899944629797  64.287240  999   
2  4621030304810285220   3.956838  100   

                                            geometry       DTTR           PHR  
0  LINESTRING (714262.483 5578857.42, 714269.543 ...   7.780674  3.348380e-25  
1  LINESTRING (713738.297 5579219.902, 713793.23 ...  64.287240  3.057601e-24  
2  LINESTRING (713650.613 5578990.488, 713649.498...   0.002291  8.354341e-04